In [31]:
import os
import pandas as pd
import numpy as np
import sys
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

비보호좌회전, 신호우회전, 유턴

줄임말 목록
- `i` : 교차로번호, `inter_no`
- `f` : 진입, from, `inc_edge_id`
- `t` : 진출, to, `out_edge_id`
- `vec` : 방향벡터, unit vector (`np.array([0.6, 0.8])`)
- `dire` : 방위, direction (동, 서, 남, 북, 북동, 북서, 남동, 남서)
- `rvec` : 정방향 방향벡터, unit vector to the right direction (`np.array([0,1])`)

필요한 객체들 목록

- `inter2dire2rvec` : `inter_no` $\mapsto$ `dire2rvec`
  - `dire2rvec` : `dire` $\mapsto$ `rvec`
- `inter2incs` : `inter_no` $\mapsto$ `inc_edge_ids`
- `inter2outs` : `inter_no` $\mapsto$ `out_edge_ids`
- `inter2inc2dire` : `inter_no` $\mapsto$ `int2dire`
  - `inc2dire` : `out_edge_id` $\mapsto$ `dire`
- `inter2out2dire` : `inter_no` $\mapsto$ `out2dire`
  - `out2dire` : `inc_edge_id` $\mapsto$ `dire`
- `inter2inc2vec` : `inter_no` $\mapsto$ `int2vec`
  - `inc2vec` : `out_edge_id` $\mapsto$ `vec`
- `inter2out2vec` : `inter_no` $\mapsto$ `out2vec`
  - `out2vec` : `inc_edge_id` $\mapsto$ `vec`

좌회전 판단

Given `inter_no`, `inc_edge_id` and `out_edge_id`, we have `inc_vec = inter2inc2vec[inter_no][inc_edge_id]` and `out_vec = inter2out2vec[inter_no][out_edge_id]`.
Rotate `inc_vec` by 90, 180 and 270 degrees clockwise, to define 
`out_vec_left`, `out_vec_straight` and `out_vec_right`.
Define `out_vecs={'right':out_vec_left, 'straight':out_vec_straight, 'right':out_vec_right}`.
Select the key that maximize the similarity of the corresponding value of the key and `inc_vec`.

In [32]:
self = DailyPreprocessor()
self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()
display(self.u_turn)

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.


parent_id child_id  adj_inc_edge_id adj_out_edge_id      inc_edge_id  \
0        i0      u00    -571500487_01    571500487_01     571500487_02   
1        i2      u20     571542811_02    571542811_01  571542810_01.51   
2        i3      u30     571556450_02    571556450_01     571556452_01   
3        i3      u31    -571500475_01    571500475_01     571500475_02   
4        i3      u32  571540303_02.21    571540303_01     571540303_02   
5        i6      u60  571500535_02.18    571500535_01     571500535_02   

       out_edge_id  
0  571500487_01.32  
1     571542810_02  
2     571556452_02  
3  571500475_01.26  
4    -571540303_02  
5    -571500535_02

In [33]:
self.u_turn = pd.merge(self.u_turn, self.u_condition, on='child_id')

# p2inc_edge2angle : node_id to inc_edge2angle
p2inc_edge2angle = dict()
# p2out_edge2angle : node_id to out_edge2angle
p2out_edge2angle = dict()
# p2inc_angle2edge : node_id to inc_angle2edge
p2inc_angle2edge = dict()
# p2out_angle2edge : node_id to out_angle2edge
p2out_angle2edge = dict()
for node_id in self.parent_ids:
    m5 = self.match5[self.match5.node_id==node_id]
    m5 = m5.dropna(subset=['inc_edge_id', 'out_edge_id'])
    # inc_edge2angle : inc_edge_id to inc_angle
    inc_edge2angle = dict(zip(m5.inc_edge_id, m5.inc_angle.astype(int)))
    p2inc_edge2angle[node_id] = inc_edge2angle
    # out_edge2angle : out_edge_id to out_angle
    out_edge2angle = dict(zip(m5.out_edge_id, m5.out_angle.astype(int)))
    p2out_edge2angle[node_id] = out_edge2angle
    # inc_angle2edge : inc_angle to inc_edge_id
    inc_angle2edge = dict(zip(m5.inc_angle.astype(int), m5.inc_edge_id))
    p2inc_angle2edge[node_id] = inc_angle2edge
    # out_angle2edge : out_angle to out_edge_id
    out_angle2edge = dict(zip(m5.out_angle.astype(int), m5.out_edge_id))
    p2out_angle2edge[node_id] = out_angle2edge

self.uid2uindex = dict() # u_turn node id to u_turn index

# 각 uturn node에 대하여 (inc_edge_id, out_edge_id) 부여
cmatches = []
for row in self.u_turn.itertuples():
    parent_id = row.parent_id
    child_id = row.child_id
    condition = row.condition
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    adj_inc_edge_id = row.adj_inc_edge_id
    adj_out_edge_id = row.adj_out_edge_id
    
    # self.uid2uindex 지정
    inc_edge = self.net.getEdge(inc_edge_id)
    out_edge = self.net.getEdge(out_edge_id)
    u_turn_conn = inc_edge.getConnections(out_edge)[0]
    self.uid2uindex[child_id] = u_turn_conn.getTLLinkIndex()
    
    # match5에서 부모노드id에 해당하는 행들을 가져옴 (cmatch)
    cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
    cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
    cmatch['node_id'] = child_id

    # 진입엣지 각도
    inc_angle = p2inc_edge2angle[parent_id][adj_inc_edge_id]

    # 이격각도
    self.angle_separation = 10

    # 진입로 각도 목록
    inc_angles = cmatch.dropna(subset=['inc_angle', 'out_angle']).inc_angle.astype(int).unique()
    inc_angles = np.sort(inc_angles)
    inc_angles = list(inc_angles - 360) + list(inc_angles) + list(inc_angles + 360)
    inc_angles = np.array(inc_angles)

    # 보행신호시의 진입로 각도
    inc_angles_left = inc_angles[inc_angles >= inc_angle + self.angle_separation]
    inc_angle_pedes = np.sort(inc_angles_left)[0] % 360

    # 보행신호시의 진입로 엣지id
    inc_angle2edge = p2inc_angle2edge[parent_id]
    inc_edge_id_pedes = inc_angle2edge[inc_angle_pedes]

    # 진출로 각도 목록
    out_angles = cmatch.dropna(subset=['inc_angle', 'out_angle']).out_angle.astype(int).unique()
    out_angles = np.sort(out_angles)
    out_angles = list(out_angles - 360) + list(out_angles) + list(out_angles + 360)
    out_angles = np.array(out_angles)

    # 보행신호시의 진입로 각도
    out_angles_right = out_angles[out_angles <= inc_angle - self.angle_separation]
    out_angle_pedes = np.sort(out_angles_right)[-1] % 360

    # 보행신호시의 진입로 엣지id
    out_angle2edge = p2out_angle2edge[parent_id]
    out_edge_id_pedes = out_angle2edge[out_angle_pedes]

    # 진입엣지/진출엣지 포함 조건
    inc_true = (cmatch.inc_edge_id==adj_inc_edge_id)
    out_true = (cmatch.out_edge_id==adj_out_edge_id)

    # 보행신호시 조건
    pedes_flag = (cmatch.inc_edge_id==inc_edge_id_pedes) & (cmatch.out_edge_id==out_edge_id_pedes)

    # 좌회전시 조건
    right_flag = inc_true & (cmatch.turn_type=='left')

    # 보행신호이동류(17) 조건
    crosswalk_on = (cmatch.move_no==17) & ~ out_true

    # 신호없음이동류(18) 조건
    all_redsigns = (cmatch.move_no==18) & ~ out_true

    # 보행신호시/좌회전시 진입/진출 엣지id 배정
    cmatch[['inc_edge_id', 'out_edge_id']] = np.nan
    if condition == "보행신호시":
        cmatch.loc[pedes_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
    elif condition == "좌회전시":
        cmatch.loc[right_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]

    uturn_not_assigned = cmatch[['inc_edge_id','out_edge_id']].isna().any(axis=1).all()

    if uturn_not_assigned:
        # 좌회전시
        if right_flag.any():
            cmatch.loc[right_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 보행신호시
        elif pedes_flag.any():
            cmatch.loc[pedes_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 보행신호이동류(17) 발생시
        elif crosswalk_on.any():
            cmatch.loc[crosswalk_on, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 신호없음이동류(18) 발생시
        elif all_redsigns.any():
            cmatch.loc[all_redsigns, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 진출엣지 미포함시
        elif out_true.any():
            cmatch.loc[~ out_true, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
    cmatches.append(cmatch)

# 각 연등교차로(coordination node)에 대하여 (inc_edge_id, out_edge_id) 부여
self.coord['inter_no'] = self.coord['parent_id'].map(self.node2inter)
self.coord = self.coord.rename(columns={'child_id':'node_id'})
self.coord[['inc_dire', 'out_dire', 'inc_angle','out_angle']] = np.nan
self.coord['move_no'] = 20
self.coord = self.coord[['inter_no', 'phase_no', 'ring_type', 'move_no', 'inc_dire', 'out_dire', 'inc_angle','out_angle', 'inc_edge_id', 'out_edge_id', 'node_id']]

cmatches = pd.concat(cmatches)
self.match6 = pd.concat([self.match5, cmatches, self.coord]).drop_duplicates().sort_values(by=['inter_no', 'node_id', 'phase_no', 'ring_type'])
self.match6 = self.match6.reset_index(drop=True)

In [36]:
for child_id in self.u_turn_ids:
    print(child_id, self.uid2uindex[child_id])
    print()

u00 4

u20 2

u30 4

u31 4

u32 7

u60 8

